In [1]:
import streamlit as st
import time
import numpy as np
import pandas as pd
import plotly.express as px
import datetime
from google.cloud import bigquery
import mysql.connector
from dotenv import load_dotenv
from google.oauth2 import service_account
from tableone import TableOne, load_dataset
import re
import seaborn as sns
import matplotlib.pyplot as plt
import time 
import numpy as np
import matplotlib.pyplot as plt
from scipy import stats

In [2]:
def identify_columns_with_units(df):
    columns_with_units = []
    for column in df.columns:
        if df[column].dtype == object:  # Considera apenas colunas com strings
            sample_value = df[column].dropna().iloc[0]  # Pega um valor não nulo para amostra
            if isinstance(sample_value, str) and re.search(r'\d', sample_value):
                columns_with_units.append(column)
    return columns_with_units

# Função para remover unidades de medida e deixar apenas o valor numérico
def remove_units(df, columns):
    for column in columns:
        # Usar expressão regular para capturar números com opcional ponto decimal
        df[column] = df[column].str.extract(r'(\d+(\.\d+)?)')[0]
        # Converter para float, ignorando erros
        df[column] = pd.to_numeric(df[column], errors='coerce')
    return df

# verificar se um valor é numérico
def is_number(s):
    if ((s == float) or (s == int)):
        try:
            float(s)
            #print(f'### A VA {s} É NUMERO')
            return True
        except ValueError:
            return False

# verificar se todas as células de uma coluna são numéricas
def convert_columns_to_numeric(df):
    for column in df.columns:
        if all(is_number(val) for val in df[column]):
            #print(f'## CONVERTENDO O TIPO DA COLUNA = {column} para float')
            df[column] = df[column].astype(float)
    return df

# Função para converter colunas para True/False e tipo booleano
def convert_columns_to_boolean(df, columns):
    for col in columns:
        df[col] = df[col].replace({1.0: True, 2.0: False}).astype(bool)
    return df

# Função para converter colunas para True/False e tipo booleano
def convert_columns_to_boolean_zero(df, columns):
    for col in columns:
        df[col] = df[col].replace({0.0: True, 1.0: False}).astype(bool)
    return df

def only_nunbers_tb1(df):
    only_nunbers = [col for col in df.columns if ((df[col].dtype == float) or (df[col].dtype == int))]
    return only_nunbers

def get_col(df):
    all_cols = [col for col in df.columns]
    return all_cols

def only_datas(df):
    datas_only = [col for col in df.columns if pd.api.types.is_datetime64_any_dtype(df[col])]    
    return datas_only

In [3]:
def conn_sql(query):
    # credentials
    usuario = 
    pwd = 
    host = 
    db = 
    
    load_dotenv() 
    
    key_path = "/home/jimi//dashboard/env.json"
    
    credentials = service_account.Credentials.from_service_account_file(
        filename=key_path, scopes=["https://www.googleapis.com/auth/cloud-platform"],
    )
    
    client = bigquery.Client(credentials=credentials, project=credentials.project_id,)

    cnx = mysql.connector.connect(user=usuario, password=pwd, host=host, database=db)
    
    # Create a cursor object
    cursor = cnx.cursor()
    
    # Execute the query
    cursor.execute(query)
    
    # Fetch all the rows
    results = cursor.fetchall()
    
    # Close the cursor and connection
    cursor.close()
    cnx.close()

    return results

In [4]:
def conn_bg(sql_statement):

    load_dotenv() 
    
    key_path = "/home/jimi//dashboard/env.json"
    
    credentials = service_account.Credentials.from_service_account_file(
        filename=key_path, scopes=["https://www.googleapis.com/auth/cloud-platform"],
    )
    
    client = bigquery.Client(credentials=credentials, project=credentials.project_id,)

    query = client.query(sql_statement) 

    return query

In [5]:
try:
    query = f"SELECT cod_paciente, nom_paciente, dt_nascimento, sexo, createdAt FROM db_name.paciente"
    
    results = conn_sql(query)
    
    columns = ["Código do paciente", "Nome paciente", "Data de nascimento", "Sexo", "Criado em"]
    df_paciente = pd.DataFrame(results, columns=columns)
    
    # calculating age
    df_paciente['Idade'] = 0
    information = df_paciente[columns].values.flatten()
    
    new = information.tolist()
    
    c = 0
    for i, r in df_paciente.iterrows():
        dob = pd.to_datetime(new[c+2])
        crt = pd.to_datetime(new[c+4]) #aumenta c tbm
        idade_dias = (crt - dob).days
        df_paciente.at[i, 'Idade'] = idade_dias//360
        c += 5
    
    df_paciente = df_paciente.fillna(0)
    df_paciente['Idade'] = df_paciente['Idade'].astype(int)
    df_paciente = df_paciente.drop(['Data de nascimento'], axis=1)

    df_paciente.head()
    
except Exception as e:
    #st.error(f"Erro: {e}")
    print((f"Erro: {e}"))

In [6]:
try:
    sql_statement = f"SELECT * FROM WHERE cod_unidade_saude=4"
    
    query = conn_bg(sql_statement)
    
    # sql_statement = f"""
    #     SELECT * FROM `-db_name.db_name.dado_resposta` WHERE cod_unidade_saude=4 
    # """
    # query = client.query(sql_statement)    
    
    rows = []
    
    for result in query.result():
        row = {
            "cod_membro_equipe_saude": result.cod_membro_equipe_saude,
            "cod_paciente": result.cod_paciente,
            "cod_usuario": result.cod_usuario, 
            "cod_visita": result.cod_visita,
            "data_resposta": result.timestamp,
            "variavel": result.variavel,
            "valor_variavel": result.valor_variavel,
        }
        rows.append(row)
     
    columns = ['cod_paciente', 'cod_usuario', 'cod_visita', 'cod_membro_equipe_saude', 'data_resposta', 'variavel', 'valor_variavel']
    df_bq = pd.DataFrame(rows, columns=columns)
    df_bq = df_bq.drop_duplicates(subset=['cod_paciente', 'variavel'], keep='last')
    
    df_pivot = df_bq.pivot_table(index='cod_paciente', columns='variavel', values='valor_variavel', aggfunc='last').reset_index()
    result_df = df_pivot #.drop('cod_paciente', axis=1)
    
    df_paciente = df_paciente.rename(columns={'Código do paciente': 'cod_paciente', 'Sexo': 'sexo', 'Idade': 'idade', 'Criado em':'data_resposta'})
    
    #copia do df_paciente para usar nos filtros de datas
    df_paciente_filto_datas = df_paciente
    
    df_merge_left = pd.merge(result_df, df_paciente, how="left", on=['cod_paciente'])
    
    df_completo = df_merge_left
    df_completo.head()

except Exception as e:
     #st.error(f"Erro: {e}")
     print((f"Erro: {e}"))

In [7]:
df_completo.head()

cod_paciente a2cd_lv_area a2cd_lv_lenght a2cd_lv_vol a2cs_lv_area  \
0            95          NaN            NaN         NaN          NaN   
1          3206     31.3 cm²        8.70 cm     88.8 ml     17.2 cm²   
2          3207     36.6 cm²        9.85 cm      107 ml     17.1 cm²   
3          3208          NaN            NaN         NaN          NaN   
4          3209     28.7 cm²        8.71 cm     82.6 ml     20.0 cm²   

  a2cs_lv_lenght a2cs_lv_vol a4cd_lv_area a4cd_lv_area_cm2 a4cd_lv_area_cm3  \
0            NaN         NaN          NaN              NaN              NaN   
1        7.15 cm     33.3 ml     33.1 cm²         33.1 cm²         14.8 cm²   
2        7.96 cm     30.2 ml     34.4 cm²         34.4 cm²         20.2 cm²   
3            NaN         NaN          NaN              NaN              NaN   
4        7.97 cm     44.9 ml     31.4 cm²         31.4 cm²         16.4 cm²   

   ... vevd_medio viae vol_diast_ae_2c vol_diast_ae_4c volume_mm weight  \
0  ...        NaN  NaN             NaN             NaN       NaN    NaN   
1  ...        NaN  NaN             NaN             NaN       NaN    NaN   
2  ...        NaN  NaN             NaN             NaN       NaN    NaN   
3  ...        NaN  NaN             NaN             NaN       NaN    NaN   
4  ...        NaN  NaN             NaN             NaN       NaN    NaN   

                   Nome paciente       sexo       data_resposta idade  
0   Paciente 2 do Clarity Health  Masculino 2022-10-27 14:22:14    44  
1  MIGUEL ALBERTO ANTUNEZ NOGUEI  Masculino 2024-04-09 19:35:28    71  
2        DIEGO DE SOUZA OLIVEIRA  Masculino 2024-04-09 19:35:28    42  
3   PAULO CESAR CORREA DE BARROS  Masculino 2024-04-09 19:35:28    31  
4   VERA CARLA DOS SANTOS BORGES   Feminino 2024-04-09 19:35:28    59  

[5 rows x 329 columns]

In [8]:
progress_bar = st.progress(0)
status_text = st.empty()

# Consulta para contar o número total de resultados
count_sql_statement = "SELECT COUNT(*) AS total FROM `-db_name.db_name.dado_resposta` WHERE cod_unidade_saude=4"

# Executa a consulta e obtém o total de resultados
count_query = conn_bg(count_sql_statement)
total_results = next(count_query.result()).total  # Usando 'next()' para acessar o primeiro resultado

# Consulta principal
sql_statement = f"SELECT * FROM  WHERE cod_unidade_saude=4"
query = conn_bg(sql_statement)

rows = []

# Loop para processar os resultados e atualizar a barra de progresso
for i, result in enumerate(query.result()):
    row = {
        "cod_membro_equipe_saude": result.cod_membro_equipe_saude,
        "cod_paciente": result.cod_paciente,
        "cod_usuario": result.cod_usuario, 
        "cod_visita": result.cod_visita,
        "data_resposta": result.timestamp,
        "variavel": result.variavel,
        "valor_variavel": result.valor_variavel,
    }
    rows.append(row)
    
    # Atualizando a barra de progresso
    #progress_bar.progress((i + 1) / total_results)
    print((i + 1) / total_results)

# Limpa a barra de progresso
progress_bar.empty()

columns = ['cod_paciente', 'cod_usuario', 'cod_visita', 'cod_membro_equipe_saude', 'data_resposta', 'variavel', 'valor_variavel']
df_bq = pd.DataFrame(rows, columns=columns)
df_bq = df_bq.drop_duplicates(subset=['cod_paciente', 'variavel'], keep='last')

df_pivot = df_bq.pivot_table(index='cod_paciente', columns='variavel', values='valor_variavel', aggfunc='last').reset_index()
result_df = df_pivot #.drop('cod_paciente', axis=1)

df_paciente = df_paciente.rename(columns={'Código do paciente': 'cod_paciente', 'Sexo': 'sexo', 'Idade': 'idade', 'Criado em':'data_resposta'})

#copia do df_paciente para usar nos filtros de datas
df_paciente_filto_datas = df_paciente

df_merge_left = pd.merge(result_df, df_paciente, how="left", on=['cod_paciente'])

#####################################################################################################
############### df_completo E df_merge_left TEM OS DADOS JUNTOS ENTRE FIREBASE E BIGQ
#####################################################################################################
df_completo = df_merge_left
#####################################################################################################
############### df_completo E df_merge_left TEM OS DADOS JUNTOS ENTRE FIREBASE E BIGQ
#####################################################################################################

#st.write("## DF COMPLETO")
#st.dataframe(df_completo)

#####################################################################################################
############### PEGA OS DADOS DO USUARIO AS VARIAVEIS DO BIGQUERY
#####################################################################################################

df_completo.at[1149, 'sexo'] = 'Feminino'

df_completo = df_completo.dropna(thresh=200, axis=1)

# Identificar colunas com valores numéricos e unidades de medida
columns_to_process = identify_columns_with_units(df_completo)

# Remover unidades de medida e deixar apenas o valor numérico
df_completo = remove_units(df_completo, columns_to_process)

df_completo = convert_columns_to_numeric(df_completo)

columns_to_process = identify_columns_with_units(df_completo)
df_completo = remove_units(df_completo, columns_to_process)
df_completo = convert_columns_to_numeric(df_completo)

# convertendo 0 e 1 para float
columns_to_convert_zero = [
    "neuropatia_diabetica", 
    "hipoglicemiantes", 
    "insulina_sim_n_o", 
]

# Lista de colunas a serem convertidas
columns_to_convert = [
    "estatina_v2", 
    "vasodilatador_v2", 
    "ieca_v2", 
    "diuretico_v2", 
    "bra_v2", 
    "bcc_v2"
]

df_completo = convert_columns_to_boolean(df_completo, columns_to_convert)
df_completo = convert_columns_to_boolean_zero(df_completo, columns_to_convert_zero)

#####################################################################################################
############### PREPARANDO PARA A TABELA 1 COM TRESHOLD
#####################################################################################################

df_tabela1 = df_completo
df_tabela1 = df_tabela1.drop(['cod_paciente', 'dxa_preenchido_por', 'Nome paciente'], axis=1)

colunas_com_data = [col for col in df_tabela1.columns if 'data' in col.lower()]

for cols in df_tabela1.columns:
    if cols in colunas_com_data:
        df_tabela1[cols] = pd.to_datetime(df_tabela1[cols], format='mixed')

datas = only_datas(df_tabela1)
columns = get_col(df_tabela1)
continuous = only_nunbers_tb1(df_tabela1)#pd.set_option('display.max_columns', None)
#pd.set_option('display.max_rows', None)
categorical = ['sexo']

#mytable = TableOne(df_tabela1, columns, categorical, continuous)
 
df_tabela_teste_drop_com_trash = df_tabela1.dropna(thresh=600, axis=1)

### tavleone like a DF
table1 = TableOne(df_tabela_teste_drop_com_trash, dip_test=True, normal_test=True, tukey_test=True)
table1

2024-09-26 11:16:46.855 
  command:

    streamlit run /home/jimi/.local/lib/python3.12/site-packages/ipykernel_launcher.py [ARGUMENTS]


4.453450310628159e-06
8.906900621256318e-06
1.3360350931884478e-05
1.7813801242512636e-05
2.2267251553140797e-05
2.6720701863768955e-05
3.117415217439712e-05
3.562760248502527e-05
4.008105279565343e-05
4.4534503106281595e-05
4.898795341690975e-05
5.344140372753791e-05
5.789485403816607e-05
6.234830434879423e-05
6.680175465942238e-05
7.125520497005054e-05
7.57086552806787e-05
8.016210559130687e-05
8.461555590193503e-05
8.906900621256319e-05
9.352245652319134e-05
9.79759068338195e-05
0.00010242935714444766
0.00010688280745507582
0.00011133625776570398
0.00011578970807633214
0.00012024315838696029
0.00012469660869758847
0.0001291500590082166
0.00013360350931884476
0.00013805695962947293
0.0001425104099401011
0.00014696386025072925
0.0001514173105613574
0.00015587076087198557
0.00016032421118261373
0.0001647776614932419
0.00016923111180387006
0.00017368456211449822
0.00017813801242512638
0.0001825914627357545
0.00018704491304638267
0.00019149836335701084
0.000195951813667639
0.000200405263

/tmp/ipykernel_55367/3225869809.py:14: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df[column] = df[column].str.extract(r'(\d+(\.\d+)?)')[0]
/tmp/ipykernel_55367/3225869809.py:16: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df[column] = pd.to_numeric(df[column], errors='coerce')
/tmp/ipykernel_55367/3225869809.py:14: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: htt

Missing                                     Overall
n                                                                                         1157
area_superficie, mean (SD)                     212                                   2.1 (3.2)
bcc_v2, n (%)                    False                                              139 (12.0)
                                 True                                              1018 (88.0)
beta_bloqueador_v2, n (%)        0.0                                                   2 (0.2)
                                 1.0                                                705 (60.9)
                                 2.0                                                216 (18.7)
                                 None                                               234 (20.2)
bra_v2, n (%)                    False                                              388 (33.5)
                                 True                                               769 (66.5)
diuretico_v2, n (%)              False                                              272 (23.5)
                                 True                                               885 (76.5)
estatina_v2, n (%)               False                                              401 (34.7)
                                 True                                               756 (65.3)
ezetimiba_v2, n (%)              0.0                                                   3 (0.3)
                                 1.0                                                895 (77.4)
                                 2.0                                                  25 (2.2)
                                 None                                               234 (20.2)
hipoglicemiantes, n (%)          False                                              831 (71.8)
                                 True                                               326 (28.2)
ieca_v2, n (%)                   False                                              120 (10.4)
                                 True                                              1037 (89.6)
insulina_sim_n_o, n (%)          False                                              175 (15.1)
                                 True                                               982 (84.9)
neuropatia_diabetica, n (%)      False                                              227 (19.6)
                                 True                                               930 (80.4)
percentil_imt_medio_d, n (%)     1.0                                                311 (26.9)
                                 2.0                                                 105 (9.1)
                                 3.0                                                  81 (7.0)
                                 4.0                                                515 (44.5)
                                 9.0                                                  55 (4.8)
                                 None                                                 90 (7.8)
percentil_imt_medio_e, mean (SD)                89                                   3.2 (2.6)
vasodilatador_v2, n (%)          False                                                14 (1.2)
                                 True                                              1143 (98.8)
sexo, n (%)                                                                            1 (0.1)
                                 Feminino                                           474 (41.0)
                                 Masculino                                          682 (58.9)
data_resposta, mean (SD)                         0  1712816925931720192.0 (1353414302086066.8)
idade, mean (SD)                                 0                                  63.7 (9.1)
[1] Hartigan's Dip Test reports possible
                                    multimodal distributions for: percentil_imt_medio_e, data_resposta, ida

In [9]:
#####################################################################################################
############### funções aux
#####################################################################################################
# Função para identificar colunas com valores numéricos e unidades de medida
def identify_columns_with_units(df):
    columns_with_units = []
    for column in df.columns:
        if df[column].dtype == object:  # Considera apenas colunas com strings
            sample_value = df[column].dropna().iloc[0]  # Pega um valor não nulo para amostra
            if isinstance(sample_value, str) and re.search(r'\d', sample_value):
                columns_with_units.append(column)
    return columns_with_units

# Função para remover unidades de medida e deixar apenas o valor numérico
def remove_units(df, columns):
    for column in columns:
        # Usar expressão regular para capturar números com opcional ponto decimal
        df[column] = df[column].str.extract(r'(\d+(\.\d+)?)')[0]
        # Converter para float, ignorando erros
        df[column] = pd.to_numeric(df[column], errors='coerce')
    return df

# verificar se um valor é numérico
def is_number(s):
    if ((s == float) or (s == int)):
        try:
            float(s)
            #print(f'### A VA {s} É NUMERO')
            return True
        except ValueError:
            return False

# verificar se todas as células de uma coluna são numéricas
def convert_columns_to_numeric(df):
    for column in df.columns:
        if all(is_number(val) for val in df[column]):
            #print(f'## CONVERTENDO O TIPO DA COLUNA = {column} para float')
            df[column] = df[column].astype(float)
    return df

# Função para converter colunas para True/False e tipo booleano
def convert_columns_to_boolean(df, columns):
    for col in columns:
        df[col] = df[col].replace({1.0: True, 2.0: False}).astype(bool)
    return df

# Função para converter colunas para True/False e tipo booleano
def convert_columns_to_boolean_zero(df, columns):
    for col in columns:
        df[col] = df[col].replace({0.0: True, 1.0: False}).astype(bool)
    return df

def only_nunbers_tb1(df):
    only_nunbers = [col for col in df.columns if ((df[col].dtype == float) or (df[col].dtype == int))]
    return only_nunbers

def get_col(df):
    all_cols = [col for col in df.columns]
    return all_cols

def only_datas(df):
    datas_only = [col for col in df.columns if pd.api.types.is_datetime64_any_dtype(df[col])]    
    return datas_only

In [12]:
df_paciente = df_paciente.rename(columns={'Código do paciente': 'cod_paciente', 'Sexo': 'sexo', 'Idade': 'idade', 'Criado em':'data_resposta'})

#copia do df_paciente para usar nos filtros de datas
df_paciente_filto_datas = df_paciente

df_merge_left = pd.merge(result_df, df_paciente, how="left", on=['cod_paciente'])

In [13]:
df_completo = df_merge_left

In [14]:
df_completo.head()

cod_paciente a2cd_lv_area a2cd_lv_lenght a2cd_lv_vol a2cs_lv_area  \
0            95          NaN            NaN         NaN          NaN   
1          3206     31.3 cm²        8.70 cm     88.8 ml     17.2 cm²   
2          3207     36.6 cm²        9.85 cm      107 ml     17.1 cm²   
3          3208          NaN            NaN         NaN          NaN   
4          3209     28.7 cm²        8.71 cm     82.6 ml     20.0 cm²   

  a2cs_lv_lenght a2cs_lv_vol a4cd_lv_area a4cd_lv_area_cm2 a4cd_lv_area_cm3  \
0            NaN         NaN          NaN              NaN              NaN   
1        7.15 cm     33.3 ml     33.1 cm²         33.1 cm²         14.8 cm²   
2        7.96 cm     30.2 ml     34.4 cm²         34.4 cm²         20.2 cm²   
3            NaN         NaN          NaN              NaN              NaN   
4        7.97 cm     44.9 ml     31.4 cm²         31.4 cm²         16.4 cm²   

   ... vevd_medio viae vol_diast_ae_2c vol_diast_ae_4c volume_mm weight  \
0  ...        NaN  NaN             NaN             NaN       NaN    NaN   
1  ...        NaN  NaN             NaN             NaN       NaN    NaN   
2  ...        NaN  NaN             NaN             NaN       NaN    NaN   
3  ...        NaN  NaN             NaN             NaN       NaN    NaN   
4  ...        NaN  NaN             NaN             NaN       NaN    NaN   

                   Nome paciente       sexo       data_resposta idade  
0   Paciente 2 do Clarity Health  Masculino 2022-10-27 14:22:14    44  
1  MIGUEL ALBERTO ANTUNEZ NOGUEI  Masculino 2024-04-09 19:35:28    71  
2        DIEGO DE SOUZA OLIVEIRA  Masculino 2024-04-09 19:35:28    42  
3   PAULO CESAR CORREA DE BARROS  Masculino 2024-04-09 19:35:28    31  
4   VERA CARLA DOS SANTOS BORGES   Feminino 2024-04-09 19:35:28    59  

[5 rows x 329 columns]

In [30]:
for col in df_completo.columns:
    print (col)

cod_paciente
a2cd_lv_area
a2cd_lv_lenght
a2cd_lv_vol
a2cs_lv_area
a2cs_lv_lenght
a2cs_lv_vol
a4cd_lv_area
a4cd_lv_area_cm2
a4cd_lv_area_cm3
a4cd_lv_area_cm4
a4cd_lv_area_cm5
a4cd_lv_lenght
a4cd_lv_length_cm
a4cd_lv_length_cm_2
a4cd_lv_length_cm_3
a4cd_lv_length_cm_4
a4cd_lv_vol
a4cd_lv_vol_ml
a4cd_lv_vol_ml_2
a4cd_lv_vol_ml_3
a4cd_lv_vol_ml_4
a4cs_lv_area
a4cs_lv_lenght
a4cs_lv_vol
adventicia_d_1
adventicia_d_2
adventicia_d_3
adventicia_d_avg
adventicia_e_1
adventicia_e_2
adventicia_e_3
adventicia_e_avg
agatston
age_data
age_risco_cdv
ant_e_vel
ao_ann_diam_dist
ao_ann_diam_dist_cm
ao_arch_diam_dist
ao_arch_diam_dist_cm
ao_sinus_diam_dist
ao_sinus_diam_dist_cm
ao_stj_diam_dist
ao_stj_diam_dist_cm
aorta_ascendente
aorta_estenose
aorta_seio_valsava
aortica_insuf
apresentou_desfecho_revasc
apresentou_desfecho_revasc_v2
apresentou_desfecho_revasc_v2_v3
area_superficie
asc_ao_diam_dist
asc_ao_diam_dist_cm
atrial_area
atrial_volume
atrio_esquerdo
av_vmax_max_pg
av_vmax_max_pg_mmhg
avddiast
av

In [33]:
desfechos = ['apresentou_desfecho_revasc',
            'apresentou_desfecho_revasc_v2',
            'apresentou_desfecho_revasc_v2_v3',
            'data_do_desfecho',
            'data_do_desfecho_v2',
            'evento_adverso_s_rio_v2',
            'evento_adverso_s_rio_v2_v3_v4_v5',
            'morte',
            'morte_v2',
            'data_do_desfecho_v2_v3_v4_v5',
            ]

# Filtra o DataFrame para as variáveis selecionadas
df_selecionado = df_completo[desfechos]

In [43]:
print(df_selecionado.to_string())

      apresentou_desfecho_revasc  apresentou_desfecho_revasc_v2  apresentou_desfecho_revasc_v2_v3  data_do_desfecho  data_do_desfecho_v2  evento_adverso_s_rio_v2  evento_adverso_s_rio_v2_v3_v4_v5  morte  morte_v2  data_do_desfecho_v2_v3_v4_v5
0                            NaN                            NaN                               NaN               NaN                  NaN                      NaN                               NaN    NaN       NaN                           NaN
1                            NaN                            NaN                               NaN               NaN                  NaN                      NaN                               NaN    NaN       NaN                           NaN
2                            NaN                            NaN                               NaN               NaN                  NaN                      NaN                               NaN    NaN       NaN                           NaN
3                           

In [16]:
df_completo.at[1149, 'sexo'] = 'Feminino'

# Identificar colunas com valores numéricos e unidades de medida
columns_to_process = identify_columns_with_units(df_completo)

# Remover unidades de medida e deixar apenas o valor numérico
df_completo = remove_units(df_completo, columns_to_process)

df_completo = convert_columns_to_numeric(df_completo)

columns_to_process = identify_columns_with_units(df_completo)
df_completo = remove_units(df_completo, columns_to_process)
df_completo = convert_columns_to_numeric(df_completo)

# convertendo 0 e 1 para float
columns_to_convert_zero = [
    "neuropatia_diabetica", 
    "hipoglicemiantes", 
    "insulina_sim_n_o", 
]

# Lista de colunas a serem convertidas
columns_to_convert = [
    "estatina_v2", 
    "vasodilatador_v2", 
    "ieca_v2", 
    "diuretico_v2", 
    "bra_v2", 
    "bcc_v2"
]

df_completo = convert_columns_to_boolean(df_completo, columns_to_convert)
df_completo = convert_columns_to_boolean_zero(df_completo, columns_to_convert_zero)

In [17]:
#####################################################################################################
############### PREPARANDO PARA A TABELA 1 COM TRESHOLD
#####################################################################################################

df_tabela1 = df_completo
df_tabela1 = df_tabela1.drop(['cod_paciente',
                          'descricao_do_evento_v2_v3_v4', 
                          'dxa_preenchido_por', 
                          'eco_observa',
                          'Nome paciente',
                          'observacoes_ecg'], axis=1)

colunas_com_data = [col for col in df_tabela1.columns if 'data' in col.lower()]

for cols in df_tabela1.columns:
    if cols in colunas_com_data:
        df_tabela1[cols] = pd.to_datetime(df_tabela1[cols], format='mixed')

datas = only_datas(df_tabela1)
columns = get_col(df_tabela1)
continuous = only_nunbers_tb1(df_tabela1)#pd.set_option('display.max_columns', None)
#pd.set_option('display.max_rows', None)
categorical = ['sexo']

#mytable = TableOne(df_tabela1, columns, categorical, continuous)
 
df_tabela_teste_drop_com_trash = df_tabela1.dropna(thresh=600, axis=1)

### tavleone like a DF
table1 = TableOne(df_tabela_teste_drop_com_trash, dip_test=True, normal_test=True, tukey_test=True)
table1
#####################################################################################################
############### tratando valores numéricos
#####################################################################################################

/home/jimi/.local/lib/python3.12/site-packages/tableone/preprocessors.py:123: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise in a future error of pandas. Value '['None' 'None' 'None' ... 'None' 'None' 'None']' has dtype incompatible with float64, please explicitly cast to a compatible dtype first.
  df.loc[:, column] = df[column].fillna(null_value)
/home/jimi/.local/lib/python3.12/site-packages/tableone/preprocessors.py:123: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise in a future error of pandas. Value '['None' 'None' 'None' ... 'None' 'None' 'None']' has dtype incompatible with float64, please explicitly cast to a compatible dtype first.
  df.loc[:, column] = df[column].fillna(null_value)
/home/jimi/.local/lib/python3.12/site-packages/tableone/preprocessors.py:123: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise in a future error of pandas. Value '['None' 'None' 'None' ... 9.0 9.

Missing                                     Overall
n                                                                                         1157
area_superficie, mean (SD)                     212                                   2.1 (3.2)
bcc_v2, n (%)                    False                                              139 (12.0)
                                 True                                              1018 (88.0)
beta_bloqueador_v2, n (%)        0.0                                                   2 (0.2)
                                 1.0                                                705 (60.9)
                                 2.0                                                216 (18.7)
                                 None                                               234 (20.2)
bra_v2, n (%)                    False                                              388 (33.5)
                                 True                                               769 (66.5)
diuretico_v2, n (%)              False                                              272 (23.5)
                                 True                                               885 (76.5)
estatina_v2, n (%)               False                                              401 (34.7)
                                 True                                               756 (65.3)
ezetimiba_v2, n (%)              0.0                                                   3 (0.3)
                                 1.0                                                895 (77.4)
                                 2.0                                                  25 (2.2)
                                 None                                               234 (20.2)
hipoglicemiantes, n (%)          False                                              831 (71.8)
                                 True                                               326 (28.2)
ieca_v2, n (%)                   False                                              120 (10.4)
                                 True                                              1037 (89.6)
insulina_sim_n_o, n (%)          False                                              175 (15.1)
                                 True                                               982 (84.9)
neuropatia_diabetica, n (%)      False                                              227 (19.6)
                                 True                                               930 (80.4)
percentil_imt_medio_d, n (%)     1.0                                                311 (26.9)
                                 2.0                                                 105 (9.1)
                                 3.0                                                  81 (7.0)
                                 4.0                                                515 (44.5)
                                 9.0                                                  55 (4.8)
                                 None                                                 90 (7.8)
percentil_imt_medio_e, mean (SD)                89                                   3.2 (2.6)
vasodilatador_v2, n (%)          False                                                14 (1.2)
                                 True                                              1143 (98.8)
sexo, n (%)                                                                            1 (0.1)
                                 Feminino                                           474 (41.0)
                                 Masculino                                          682 (58.9)
data_resposta, mean (SD)                         0  1712816925931720192.0 (1353414302086066.8)
idade, mean (SD)                                 0                                  63.7 (9.1)
[1] Hartigan's Dip Test reports possible
                                    multimodal distributions for: percentil_imt_medio_e, data_resposta, ida

In [18]:
#####################################################################################################
############### tratando valores numéricos
#####################################################################################################
df_completo.at[1149, 'sexo'] = 'Feminino'

# Identificar colunas com valores numéricos e unidades de medida
columns_to_process = identify_columns_with_units(df_completo)

# Remover unidades de medida e deixar apenas o valor numérico
df_completo = remove_units(df_completo, columns_to_process)

df_completo = convert_columns_to_numeric(df_completo)

columns_to_process = identify_columns_with_units(df_completo)
df_completo = remove_units(df_completo, columns_to_process)
df_completo = convert_columns_to_numeric(df_completo)

# convertendo 0 e 1 para float
columns_to_convert_zero = [
    "neuropatia_diabetica", 
    "hipoglicemiantes", 
    "insulina_sim_n_o", 
]

# Lista de colunas a serem convertidas
columns_to_convert = [
    "estatina_v2", 
    "vasodilatador_v2", 
    "ieca_v2", 
    "diuretico_v2", 
    "bra_v2", 
    "bcc_v2"
]

df_completo = convert_columns_to_boolean(df_completo, columns_to_convert)
df_completo = convert_columns_to_boolean_zero(df_completo, columns_to_convert_zero)


sql_statement_datas = f"""
    SELECT cod_paciente, cod_visita, cod_usuario, cod_unidade_saude, variavel, valor_variavel, cod_resposta_questionario, timestamp
    FROM `-db_name.db_name.dado_resposta` 
    WHERE cod_unidade_saude = 4;
"""#.format(data_inicial, data_final)

query = client.query(sql_statement_datas) 

rows = []
for result in query.result():
    row = {
        #'cod_unidade_saude': result.cod_membro_equipe_saude,
        "cod_paciente": result.cod_paciente,
        "cod_usuario": result.cod_usuario, 
        "cod_visita": result.cod_visita,
        "data_resposta": result.timestamp,
        "variavel": result.variavel,
        "valor_variavel": result.valor_variavel,
    }
    rows.append(row)

columns = ['cod_paciente', 'cod_usuario', 'cod_visita', 'data_resposta', 'variavel', 'valor_variavel']
df_bq = pd.DataFrame(rows, columns=columns)
df_bq = df_bq.drop_duplicates(subset=['cod_paciente', 'variavel'], keep='last')

df_pivot = df_bq.pivot_table(index='cod_paciente', columns='variavel', values='valor_variavel', aggfunc='last').reset_index()
result_df = df_pivot #.drop('cod_paciente', axis=1)

df_paciente_filto_datas = df_paciente_filto_datas.rename(columns={'Código do paciente': 'cod_paciente', 'Sexo': 'sexo', 'Idade': 'idade'})

df_merge_left = pd.merge(result_df, df_paciente_filto_datas, how="left", on=['cod_paciente'])

df_filtro_datas = df_merge_left

# Primeiro, agrupe os dados por dia e conte o número de consultas por dia
consultas_por_dia = df_filtro_datas.groupby(df_filtro_datas["data_resposta"].dt.date).size().reset_index(name='quantidade_consultas')

In [19]:
consultas_por_dia

data_resposta  quantidade_consultas
0    2022-10-27                     1
1    2024-04-09                    69
2    2024-04-11                  1086
3    2024-05-03                     1

In [20]:
#####################################################################################################
############### por questionário
#####################################################################################################

#patient data
query = f"SELECT r.cod_visita, r.status, p.cod_paciente, p.nom_paciente, p.sexo, v.dt_inicio_visita, tq.name, tq.json_template FROM `db_name`.resposta_questionario r JOIN `db_name`.visita v ON v.cod_visita = r.cod_visita JOIN `db_name`.paciente p ON p.cod_paciente = v.cod_paciente JOIN `db_name`.template_questionario tq ON tq.cod_template_questionario = r.cod_template_questionario WHERE v.cod_unidade_saude = 4 AND tq.isDeleted = 0"

cnx = mysql.connector.connect(user=usuario, password=pwd, host=host, database=db)

# Create a cursor object
cursor = cnx.cursor()

# Execute the query
cursor.execute(query)

# Fetch all the rows
results = cursor.fetchall()

# Close the cursor and connection
cursor.close()
cnx.close()
  
columns = ["cod_visita", "status", "cod_paciente", "nom_paciente", "sexo",
          "dt_inicio_visita", "name", "json_template"]

df_paciente = pd.DataFrame(results, columns=columns)

df_quests = df_paciente

# Agrupa os dados pelo nome do questionário e conta o número de ocorrências
questionario_counts = df_quests['name'].value_counts().reset_index()
questionario_counts.columns = ['name', 'count']
 
# Primeiro, agrupe os dados por dia e conte o número de consultas por dia
quests_por_dia = df_quests.groupby(df_quests["dt_inicio_visita"].dt.date).size().reset_index(name='quantidade_quests')

# Remover a hora e manter apenas ano, mês e dia
quests_por_dia["dt_inicio_visita"] = pd.to_datetime(quests_por_dia["dt_inicio_visita"]).dt.floor('D')

# Agrupando por mês e ano e contando a quantidade de consultas
quests_por_mes = df_quests.groupby(df_quests["dt_inicio_visita"].dt.to_period('M')).size().reset_index(name='quantidade_quests')
quests_por_mes["dt_inicio_visita"] = quests_por_mes["dt_inicio_visita"].dt.to_timestamp()

date = '2015-12-30'
date64 = np.datetime64(date)

#exclui as linhas com data < 2015-12-30
quests_por_mes = quests_por_mes.drop(quests_por_mes[quests_por_mes['dt_inicio_visita'] <= date64].index)

In [25]:
print(quests_por_mes['dt_inicio_visita'].to_string())

2    2016-12-01
3    2017-01-01
4    2017-02-01
5    2017-03-01
6    2017-04-01
7    2017-05-01
8    2017-06-01
9    2017-07-01
10   2017-08-01
11   2017-09-01
12   2017-10-01
13   2017-11-01
14   2017-12-01
15   2018-01-01
16   2018-02-01
17   2018-03-01
18   2018-04-01
19   2018-05-01
20   2018-06-01
21   2018-07-01
22   2018-08-01
23   2018-09-01
24   2018-10-01
25   2018-11-01
26   2018-12-01
27   2019-01-01
28   2019-02-01
29   2019-05-01
30   2019-06-01
31   2019-07-01
32   2019-08-01
33   2019-09-01
34   2019-10-01
35   2019-11-01
36   2020-01-01
37   2020-02-01
38   2020-03-01
39   2020-11-01
40   2020-12-01
41   2021-01-01
42   2021-03-01
43   2021-04-01
44   2021-08-01
45   2022-03-01
46   2022-05-01
47   2022-08-01
48   2022-09-01
49   2022-11-01
50   2022-12-01
51   2023-01-01
52   2023-02-01
53   2023-03-01
54   2023-04-01
55   2023-05-01
56   2023-06-01
57   2023-08-01
58   2023-09-01
59   2023-10-01
60   2023-11-01
61   2023-12-01
62   2024-01-01
63   2024-02-01
64   202

In [18]:
df_completo.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1157 entries, 0 to 1156
Columns: 329 entries, cod_paciente to idade
dtypes: bool(9), datetime64[ns](1), float64(310), int64(2), object(7)
memory usage: 2.8+ MB


In [19]:
df_completo

cod_paciente  a2cd_lv_area  a2cd_lv_lenght  a2cd_lv_vol  a2cs_lv_area  \
0               95           NaN             NaN          NaN           NaN   
1             3206          31.3            8.70         88.8         17.20   
2             3207          36.6            9.85        107.0         17.10   
3             3208           NaN             NaN          NaN           NaN   
4             3209          28.7            8.71         82.6         20.00   
5             3210          34.1            9.12        108.0         18.70   
6             3211           NaN             NaN          NaN           NaN   
7             3212          27.1            7.70         76.5         13.90   
8             3213          33.5            8.67        109.0         15.30   
9             3214          27.4            8.09         77.5         13.90   
10            3215          43.8            9.96        158.0         27.90   
11            3216          19.8            7.04         48.4         11.40   
12            3217          23.5            6.14         75.6         16.10   
13            3218          48.8           10.50        188.0         26.40   
14            3219          28.0            7.37         90.1         17.30   
15            3220          25.3            8.27         63.8         12.00   
16            3221           NaN             NaN          NaN           NaN   
17            3222          25.0            6.83         81.7         16.00   
18            3223          34.2            9.13        106.0         19.60   
19            3224          25.8            6.91         80.3         12.90   
20            3225          51.4            9.98        223.0         37.40   
21            3226          49.2           10.30        190.0         29.00   
22            3227          29.2            7.60         92.5         16.30   
23            3228          35.0            9.09        113.0         19.20   
24            3229          17.8            6.22         41.5          9.56   
25            3230          18.2            7.21         37.5          8.76   
26            3231           NaN             NaN          NaN           NaN   
27            3232          19.0            6.92         43.5          8.70   
28            3233           NaN             NaN          NaN           NaN   
29            3234          25.1            7.30         75.5         14.20   
30            3235          34.4            8.22        117.0         15.90   
31            3236           NaN             NaN          NaN           NaN   
32            3237          23.8            6.65         70.2          9.84   
33            3238          20.2            7.38         47.5         11.30   
34            3239           NaN             NaN          NaN           NaN   
35            3240          40.8            9.37        145.0         26.50   
36            3241          16.4            5.89         37.7          7.99   
37            3242          25.0            7.77         66.5         14.60   
38            3243          25.3            7.58         70.6         13.40   
39            3244          26.4            7.51         79.3         14.20   
40            3245          40.5            9.33        148.0         22.70   
41            3246          50.5           10.60        199.0         41.80   
42            3247          28.4            7.76         87.1         17.00   
43            3248          30.5            8.54         92.2         19.50   
44            3249          14.4            6.01         30.2          8.14   
45            3250          38.0            7.97        144.0         22.10   
46            3251          26.7            6.64         88.0         13.60   
47            3252           NaN             NaN          NaN           NaN   
48            3253           NaN             NaN          NaN           NaN   
49            3254          18.8            6.39        

In [17]:


### frontend

#pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

st.set_page_config(
    page_title="Dashboard de acompanhamento médico",
    page_icon="📋",
    layout="wide",
    initial_sidebar_state="expanded")

st.title('Dashboard ATEROLAB')

# Sidebar for selecting variables
st.sidebar.title('Menu principal')

with st.spinner("Carregando as variáveis"):
 variables = df_completo.columns.tolist() #lista que vem do dataset
 selected_variable = st.sidebar.selectbox('Escolha a variável para ver as estatisticas sobre ela', variables)

col1, col2 = st.columns(2)
col3, col4 = st.columns(2)

# Main page
st.title('Statistical Measures Dashboard')

with st.spinner("Carregando a Tabela 1"):
 df_counts = df_completo[columns_to_convert].apply(pd.Series.value_counts).T
 col1.write('TableOne - Trashold de {}%')
 col1.write(table1.tableone, unsafe_allow_html=True, use_container_width=True)

with st.spinner("Carregando os dados da variável escolhida"):
 if selected_variable:
     # Calculate statistics for the selected variable
     mean = variables[selected_variable].mean()
     median = variables[selected_variable].median()
     std_dev = variables[selected_variable].std()
     variance = variables[selected_variable].var()
     data_range = variables[selected_variable].max() - data[selected_variable].min()
     
     # Display statistics
     
     st.write(f"**Selected Variable:** {selected_variable}")
     st.write(f"**Mean:** {mean:.2f}")
     st.write(f"**Median:** {median:.2f}")
     st.write(f"**Standard Deviation:** {std_dev:.2f}")
     st.write(f"**Variance:** {variance:.2f}")
     st.write(f"**Range:** {data_range:.2f}")

2024-09-02 08:13:10.677 Session state does not function when running a script without `streamlit run`
2024-09-02 08:13:10.680 Invalid arguments were passed to "st.write" function. Support for passing such unknown keywords arguments will be dropped in future. Invalid arguments were: {'use_container_width': True}
2024-09-02 08:13:10.681 Serialization of dataframe to Arrow table was unsuccessful due to: ("Expected bytes, got a 'int' object", 'Conversion failed for column Missing with type object'). Applying automatic fixes for column types to make the dataframe Arrow-compatible.


TypeError: list indices must be integers or slices, not str

In [20]:
variaveis_numericas = df_completo.select_dtypes(include=['float', 'int']).columns.tolist()
variaveis_categóricas = df_completo.select_dtypes(include=['bool']).columns.tolist()

In [21]:
variaveis_numericas

['cod_paciente',
 'a2cd_lv_area',
 'a2cd_lv_lenght',
 'a2cd_lv_vol',
 'a2cs_lv_area',
 'a2cs_lv_lenght',
 'a2cs_lv_vol',
 'a4cd_lv_area',
 'a4cd_lv_area_cm2',
 'a4cd_lv_area_cm3',
 'a4cd_lv_area_cm4',
 'a4cd_lv_area_cm5',
 'a4cd_lv_lenght',
 'a4cd_lv_length_cm',
 'a4cd_lv_length_cm_2',
 'a4cd_lv_length_cm_3',
 'a4cd_lv_length_cm_4',
 'a4cd_lv_vol',
 'a4cd_lv_vol_ml',
 'a4cd_lv_vol_ml_2',
 'a4cd_lv_vol_ml_3',
 'a4cd_lv_vol_ml_4',
 'a4cs_lv_area',
 'a4cs_lv_lenght',
 'a4cs_lv_vol',
 'adventicia_d_1',
 'adventicia_d_2',
 'adventicia_d_3',
 'adventicia_d_avg',
 'adventicia_e_1',
 'adventicia_e_2',
 'adventicia_e_3',
 'adventicia_e_avg',
 'age_data',
 'age_risco_cdv',
 'ant_e_vel',
 'ao_ann_diam_dist',
 'ao_ann_diam_dist_cm',
 'ao_arch_diam_dist',
 'ao_arch_diam_dist_cm',
 'ao_sinus_diam_dist',
 'ao_sinus_diam_dist_cm',
 'ao_stj_diam_dist',
 'ao_stj_diam_dist_cm',
 'aorta_ascendente',
 'aorta_estenose',
 'aorta_seio_valsava',
 'aortica_insuf',
 'apresentou_desfecho_revasc',
 'apresentou_des

In [22]:
variaveis_categóricas

['bcc_v2',
 'bra_v2',
 'diuretico_v2',
 'estatina_v2',
 'hipoglicemiantes',
 'ieca_v2',
 'insulina_sim_n_o',
 'neuropatia_diabetica',
 'vasodilatador_v2']

In [32]:
variaveis_numericas = df_completo.select_dtypes(include=['float', 'int']).columns.tolist()
variaveis_categóricas = df_completo.select_dtypes(include=['bool']).columns.tolist()

In [33]:
var_numerica = df_completo.select_dtypes(include=['float', 'int']).columns.tolist() #lista que vem do dataset
#selected_variable = st.sidebar.selectbox('Escolha a variável para ver as estatisticas sobre ela', variables)
#st.markdown("<h1 style='text-align: center; color: grey;'>Dashboard Aterolab</h1>", unsafe_allow_html=True)
selected_variables_numeric = st.sidebar.multiselect('Escolha as variáveis para exibir ESTATÍSTICAS', var_numerica)

var_categrica = df_completo.select_dtypes(include=['bool']).columns.tolist() #lista que vem do dataset
#selected_variable = st.sidebar.selectbox('Escolha a variável para ver as estatisticas sobre ela', var_cat)
selected_var_cat = st.sidebar.multiselect('Escolha as variáveis para exibir ESTATÍSTICAS', var_categrica)

In [34]:
selected_variables_numeric

[]

In [22]:
print(df_completo.shape)

(1157, 329)


In [21]:
with st.spinner("Carregando os dados dos QUESTIONÁRIOS"):
  #patient data
  query = f"SELECT r.cod_visita, r.status, p.cod_paciente, p.nom_paciente, p.sexo, v.dt_inicio_visita, tq.name, tq.json_template FROM `db_name`.resposta_questionario r JOIN `db_name`.visita v ON v.cod_visita = r.cod_visita JOIN `db_name`.paciente p ON p.cod_paciente = v.cod_paciente JOIN `db_name`.template_questionario tq ON tq.cod_template_questionario = r.cod_template_questionario WHERE v.cod_unidade_saude = 4 AND tq.isDeleted = 0"
  
  cnx = mysql.connector.connect(user=usuario, password=pwd, host=host, database=db)
  
  # Create a cursor object
  cursor = cnx.cursor()
  
  # Execute the query
  cursor.execute(query)
  
  # Fetch all the rows
  results = cursor.fetchall()
  
  # Close the cursor and connection
  cursor.close()
  cnx.close()
  
  columns = ["cod_visita", "status", "cod_paciente", "nom_paciente", "sexo",
            "dt_inicio_visita", "name", "json_template"]
  
  df_paciente = pd.DataFrame(results, columns=columns)
  
  df_quests = df_paciente
  
  # Agrupa os dados pelo nome do questionário e conta o número de ocorrências
  questionario_counts = df_quests['name'].value_counts().reset_index()
  questionario_counts.columns = ['name', 'count']
  
  # Primeiro, agrupe os dados por dia e conte o número de consultas por dia
  quests_por_dia = df_quests.groupby(df_quests["dt_inicio_visita"].dt.date).size().reset_index(name='quantidade_quests')
  
  # Remover a hora e manter apenas ano, mês e dia
  quests_por_dia["dt_inicio_visita"] = pd.to_datetime(quests_por_dia["dt_inicio_visita"]).dt.floor('D')
  
  # Agrupando por mês e ano e contando a quantidade de consultas
  quests_por_mes = df_quests.groupby(df_quests["dt_inicio_visita"].dt.to_period('M')).size().reset_index(name='quantidade_quests')
  quests_por_mes["dt_inicio_visita"] = quests_por_mes["dt_inicio_visita"].dt.to_timestamp()
  
  date = '2015-12-30'
  date64 = np.datetime64(date)
  
  #exclui as linhas com data < 2015-12-30
  quests_por_mes = quests_por_mes.drop(quests_por_mes[quests_por_mes['dt_inicio_visita'] <= date64].index)

  quests_por_mes

In [22]:
quests_por_mes

dt_inicio_visita  quantidade_quests
2        2016-12-01                 13
3        2017-01-01                  7
4        2017-02-01                 42
5        2017-03-01                  4
6        2017-04-01                  2
..              ...                ...
63       2024-02-01               1074
64       2024-03-01               2574
65       2024-04-01               1064
66       2024-05-01                 19
67       2024-08-01                  1

[66 rows x 2 columns]

In [46]:
var_numerica = df_completo.select_dtypes(include=['float', 'int']).columns.tolist() #lista que vem do dataset
#selected_variable = st.sidebar.selectbox('Escolha a variável para ver as estatisticas sobre ela', variables)
#st.markdown("<h1 style='text-align: center; color: grey;'>Dashboard Aterolab</h1>", unsafe_allow_html=True)
selected_variables_numeric = st.sidebar.multiselect('Escolha as variáveis para exibir ESTATÍSTICAS', var_numerica)

var_categrica = df_completo.select_dtypes(include=['bool']).columns.tolist() #lista que vem do dataset
#selected_variable = st.sidebar.selectbox('Escolha a variável para ver as estatisticas sobre ela', var_cat)
selected_var_cat = st.sidebar.multiselect('Escolha as variáveis para exibir ESTATÍSTICAS', var_categrica)

In [49]:
stats_list = []

for variable in selected_variables_numeric:
    # Calcula as estatísticas para a variável selecionada
    mean = df_completo[variable].mean()
    median = df_completo[variable].median()
    std_dev = df_completo[variable].std()
    variance = df_completo[variable].var()
    data_range = df_completo[variable].max() - df_completo[variable].min()

    # Adiciona as estatísticas à lista como um dicionário
    stats_list.append({
        "Variável": variable,
        "Média": f"{mean:.2f}",
        "Mediana": f"{median:.2f}",
        "Desvio Padrão": f"{std_dev:.2f}",
        "Variância": f"{variance:.2f}",
        "Intervalo": f"{data_range:.2f}"
    })

# Cria um DataFrame a partir da lista de dicionários
stats_df = pd.DataFrame(stats_list)

# Exibe o DataFrame no Streamlit
col2.write("### ESTATÍSTICAS das Variáveis Numéricas")
col2.dataframe(stats_df)

DeltaGenerator()

In [48]:
stats_df

Empty DataFrame
Columns: []
Index: []

In [50]:
df_completo.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1157 entries, 0 to 1156
Columns: 329 entries, cod_paciente to idade
dtypes: bool(9), datetime64[ns](1), float64(310), int64(2), object(7)
memory usage: 2.8+ MB


In [55]:
for col in df_completo.columns:
    print(col)

cod_paciente
a2cd_lv_area
a2cd_lv_lenght
a2cd_lv_vol
a2cs_lv_area
a2cs_lv_lenght
a2cs_lv_vol
a4cd_lv_area
a4cd_lv_area_cm2
a4cd_lv_area_cm3
a4cd_lv_area_cm4
a4cd_lv_area_cm5
a4cd_lv_lenght
a4cd_lv_length_cm
a4cd_lv_length_cm_2
a4cd_lv_length_cm_3
a4cd_lv_length_cm_4
a4cd_lv_vol
a4cd_lv_vol_ml
a4cd_lv_vol_ml_2
a4cd_lv_vol_ml_3
a4cd_lv_vol_ml_4
a4cs_lv_area
a4cs_lv_lenght
a4cs_lv_vol
adventicia_d_1
adventicia_d_2
adventicia_d_3
adventicia_d_avg
adventicia_e_1
adventicia_e_2
adventicia_e_3
adventicia_e_avg
agatston
age_data
age_risco_cdv
ant_e_vel
ao_ann_diam_dist
ao_ann_diam_dist_cm
ao_arch_diam_dist
ao_arch_diam_dist_cm
ao_sinus_diam_dist
ao_sinus_diam_dist_cm
ao_stj_diam_dist
ao_stj_diam_dist_cm
aorta_ascendente
aorta_estenose
aorta_seio_valsava
aortica_insuf
apresentou_desfecho_revasc
apresentou_desfecho_revasc_v2
apresentou_desfecho_revasc_v2_v3
area_superficie
asc_ao_diam_dist
asc_ao_diam_dist_cm
atrial_area
atrial_volume
atrio_esquerdo
av_vmax_max_pg
av_vmax_max_pg_mmhg
avddiast
av

In [40]:
result_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1157 entries, 0 to 1156
Columns: 325 entries, cod_paciente to weight
dtypes: int64(1), object(324)
memory usage: 2.9+ MB


In [41]:
identify_columns_with_units(result_df)

columns_to_process = identify_columns_with_units(result_df)

result_df = convert_columns_to_numeric(result_df)

In [42]:
result_df_corr

variavel  cod_paciente
0                   95
1                 3206
2                 3207
3                 3208
4                 3209
5                 3210
6                 3211
7                 3212
8                 3213
9                 3214
10                3215
11                3216
12                3217
13                3218
14                3219
15                3220
16                3221
17                3222
18                3223
19                3224
20                3225
21                3226
22                3227
23                3228
24                3229
25                3230
26                3231
27                3232
28                3233
29                3234
30                3235
31                3236
32                3237
33                3238
34                3239
35                3240
36                3241
37                3242
38                3243
39                3244
40                3245
41                3246
42                3247
43                3248
44                3249
45                3250
46                3251
47                3252
48                3253
49                3254
50                3255
51                3256
52                3257
53                3258
54                3259
55                3260
56                3261
57                3262
58                3263
59                3264
60                3265
61                3266
62                3267
63                3268
64                3269
65                3270
66                3272
67                3273
68                3274
69                3275
70                3276
71                3277
72                3278
73                3279
74                3280
75                3281
76                3282
77                3283
78                3284
79                3285
80                3286
81                3287
82                3288
83                3289
84                3290
85                3291
86                3292
87                3293
88                3294
89                3296
90                3297
91                3298
92                3299
93                3300
94                3301
95                3302
96                3303
97                3304
98                3305
99                3306
100               3307
101               3308
102               3309
103               3310
104               3311
105               3312
106               3313
107               3314
108               3315
109               3316
110               3317
111               3318
112               3319
113               3320
114               3321
115               3322
116               3323
117               3324
118               3325
119               3326
120               3327
121               3328
122               3329
123               3330
124               3331
125               3332
126               3333
127               3334
128               3335
129               3336
130               3337
131               3338
132               3339
133               3340
134               3341
135               3342
136               3343
137               3344
138               3345
139               3346
140               3347
141               3348
142               3349
143               3350
144               3351
145               3352
146               3353
147               3354
148               3355
149               3356
150               3357
151               3358
152               3359
153               3360
154               3361
155               3362
156               3363
157               3364
158               3365
159               3366
160               3367
161               3368
162               3369
163               3370
164               3371
165               3372
166               3373
167               3374
168               3375
169               3376
170               3377
171               3378
172               337

In [59]:
# Filtra o DataFrame com base no intervalo de datas selecionado
start_date = st.sidebar.date_input('Data de início', df_completo['data_resposta'].min())
end_date = st.sidebar.date_input('Data de fim', df_completo['data_resposta'].max())

# Filtra o DataFrame com base no intervalo de datas selecionado
df_filtrado = df_completo[(df_completo['data_resposta'] >= pd.to_datetime(start_date)) & 
                          (df_completo['data_resposta'] <= pd.to_datetime(end_date))]

# Filtrando apenas as colunas numéricas
df_numerico = df_filtrado.select_dtypes(include=['float64', 'int64'])

# Resetando o índice da matriz de correlação para garantir que os rótulos apareçam
correlation_matrix = df_numerico.corr()
correlation_matrix_reset = correlation_matrix.reset_index()

correlation_matrix_reset

index  cod_paciente  a2cd_lv_area  \
0                        cod_paciente      1.000000     -0.192437   
1                        a2cd_lv_area     -0.192437      1.000000   
2                      a2cd_lv_lenght     -0.194070      0.898657   
3                         a2cd_lv_vol     -0.186937      0.986225   
4                        a2cs_lv_area     -0.131695      0.919083   
5                      a2cs_lv_lenght     -0.188047      0.842658   
6                         a2cs_lv_vol     -0.115749      0.871423   
7                        a4cd_lv_area     -0.115340      0.842558   
8                    a4cd_lv_area_cm2     -0.115340      0.842558   
9                    a4cd_lv_area_cm3     -0.083708      0.820655   
10                   a4cd_lv_area_cm4     -0.192437      1.000000   
11                   a4cd_lv_area_cm5     -0.131695      0.919083   
12                     a4cd_lv_lenght     -0.083129      0.785994   
13                  a4cd_lv_length_cm     -0.083129      0.785994   
14                a4cd_lv_length_cm_2     -0.017345      0.782369   
15                a4cd_lv_length_cm_3     -0.194070      0.898657   
16                a4cd_lv_length_cm_4     -0.188047      0.842658   
17                        a4cd_lv_vol     -0.111699      0.814573   
18                     a4cd_lv_vol_ml     -0.111699      0.814573   
19                   a4cd_lv_vol_ml_2     -0.083786      0.779503   
20                   a4cd_lv_vol_ml_3     -0.186937      0.986225   
21                   a4cd_lv_vol_ml_4     -0.115749      0.871423   
22                       a4cs_lv_area     -0.083708      0.820655   
23                     a4cs_lv_lenght     -0.017345      0.782369   
24                        a4cs_lv_vol     -0.083786      0.779503   
25                     adventicia_d_1     -0.091198           NaN   
26                     adventicia_d_2      0.030250           NaN   
27                     adventicia_d_3     -0.109653           NaN   
28                   adventicia_d_avg      0.013582           NaN   
29                     adventicia_e_1      0.094115           NaN   
30                     adventicia_e_2      0.092580           NaN   
31                     adventicia_e_3      0.090610           NaN   
32                   adventicia_e_avg     -0.092103           NaN   
33                           age_data     -0.112087           NaN   
34                      age_risco_cdv           NaN           NaN   
35                          ant_e_vel      0.013792      0.158717   
36                   ao_ann_diam_dist      0.102183      0.575182   
37                ao_ann_diam_dist_cm      0.102183      0.575182   
38                  ao_arch_diam_dist     -0.079047      0.197872   
39               ao_arch_diam_dist_cm     -0.079047      0.197872   
40                 ao_sinus_diam_dist      0.130918      0.240933   
41              ao_sinus_diam_dist_cm      0.130918      0.240933   
42                   ao_stj_diam_dist      0.184735      0.081359   
43                ao_stj_diam_dist_cm      0.184735      0.081359   
44                   aorta_ascendente      0.124562           NaN   
45                     aorta_estenose     -0.044077           NaN   
46                 aorta_seio_valsava      0.070627           NaN   
47                      aortica_insuf      0.106027           NaN   
48         apresentou_desfecho_revasc     -0.009488           NaN   
49      apresentou_desfecho_revasc_v2     -0.983123           NaN   
50   apresentou_desfecho_revasc_v2_v3      0.456630           NaN   
51                    area_superficie      0.072103           NaN   
52                   asc_ao_diam_dist      0.046265      0.225407   
53                asc_ao_diam_dist_cm      0.046265      0.225407   
54                        atrial_area     -0.093556      0.467332   
55                      atrial_volume     -0.112760      0.475848   
56                     atrio_esquerdo     -0.053956           NaN   
57                     av_vmax

In [60]:
m_o_direita_3 = df_completo['m_o_direita_3']
pa_sistolica = df_completo['pa_sistolica'] 
weight = df_completo['weight']

In [61]:
pa_sistolica

0         NaN
1         NaN
2         NaN
3         NaN
4         NaN
5         NaN
6         NaN
7         NaN
8         NaN
9         NaN
10        NaN
11        NaN
12        NaN
13        NaN
14        NaN
15        NaN
16        NaN
17        NaN
18        NaN
19        NaN
20        NaN
21        NaN
22        NaN
23        NaN
24        NaN
25        NaN
26        NaN
27        NaN
28        NaN
29        NaN
30        NaN
31        NaN
32        NaN
33        NaN
34        NaN
35        NaN
36        NaN
37        NaN
38        NaN
39        NaN
40        NaN
41        NaN
42        NaN
43        NaN
44        NaN
45        NaN
46        NaN
47        NaN
48        NaN
49        NaN
50        NaN
51        NaN
52        NaN
53        NaN
54        NaN
55        NaN
56        NaN
57        NaN
58        NaN
59        NaN
60        NaN
61        NaN
62        NaN
63        NaN
64        NaN
65        NaN
66        NaN
67        NaN
68        NaN
69        NaN
70        NaN
71    

In [43]:
stats_df

NameError: name 'stats_df' is not defined

In [24]:
#excluir colunas com strings
#print(f'shape antes de excluir {result_df.shape}\n')
result_df_corr = result_df.select_dtypes(exclude=['object'])
#print(f'shape DEPOIS de excluir {result_df_corr.shape}')

result_df_corr = df_completo.drop(['telefone_1', 
                                'telefone_contato_1',
                                'telefone_contato_2',
                                'cod_paciente',
                                'centro_de_pesquisa',
                                'classes_social_por_renda_f',
                                'cep',
                                'escolaridade',
                                'estado_civil',
                                'examinador_fmd',
                                'examinador',
                                'genero',
                                'numero_identificacao',
                                'raca',
                                'data_caminhada',
                                'data_da_consulta_id',
                                'data_de_alta_ou_morte',
                                'data_de_contato',
                                'data_de_contato_v2_v3',
                                'data_de_contato_v2_v3_v4_v5',
                                'data_densit',
                                'data_do_desfecho',
                                'data_do_desfecho_v2',
                                'data_do_desfecho_v2_v3_v4_v5',
                                'data_do_exame_nac',
                                'data_nascimento',
                                'data_retinopathy',
                               ], axis=1)


result_df_corr.corr().style.background_gradient(cmap="Blues")
correlation_matrix = df_completo.corr()
col5.write("### Tabela de Correlação")
col5.dataframe(correlation_matrix)

######################################################

KeyError: "['telefone_1', 'telefone_contato_1', 'telefone_contato_2', 'classes_social_por_renda_f', 'cep', 'escolaridade', 'numero_identificacao', 'raca', 'data_da_consulta_id', 'data_de_alta_ou_morte', 'data_nascimento'] not found in axis"

In [ ]:
# Supondo que df_completo seja seu DataFrame e tenha uma coluna de data chamada 'data_coluna'
df_completo = pd.DataFrame({
    'data_coluna': pd.date_range(start='2023-01-01', periods=365, freq='D'),
    'variavel_1': range(365),
    'variavel_2': range(365, 730)
})

# Sidebar para seleção do intervalo de datas
st.sidebar.header("Filtro por Data")
start_date = st.sidebar.date_input("Data de Início", value=pd.to_datetime("2023-01-01"))
end_date = st.sidebar.date_input("Data de Fim", value=pd.to_datetime("2023-12-31"))